In [ ]:
import sys
import os
sys.path.insert(0, os.path.abspath('../..'))
from experiments.iter1.util.importer import *
MODEL_PATH = 'model_saves/testing_model'
nist_path = "../../src/data_preprocess/dataset/UKDATA_cleaned.csv"

In [ ]:
assert time_horizon > 0, "Time horizon must be a positive integer"
    
df = pd.read_csv(nist_path)

cleaner = TempCleaner(clean_pow_low, clean_in_low, clean_in_high, clean_out_low, clean_out_high, clean_delta_temp)
splitter = StdSplitter(train_days, val_days, test_days)
    
model = LSTM(hidden_size, num_layers, input_size, time_horizon, dropout)
trainer = TrainerWrapper(L.Trainer, 
                         max_epochs=num_epochs, 
                         callbacks=[ConditionalEarlyStopping(threshold=early_stopping_threshold)], 
                         gradient_clip_val=gradient_clipping)
optimizer = OptimizerWrapper(optim.Adam, model, lr=learning_rate)

model = DeterministicPipeline.Builder() \
        .add_data(df) \
        .set_cleaner(cleaner) \
        .set_normalizer_class(MinMaxNormalizer) \
        .set_splitter(splitter) \
        .set_sequencer_class(TimeSequencer) \
        .set_target_column(TARGET_COLUMN) \
        .set_model(model) \
        .set_optimizer(optimizer) \
        .set_batch_size(batch_size) \
        .set_seq_len(seq_len) \
        .set_worker_num(NUM_WORKERS) \
        .set_error(NRMSE) \
        .set_trainer(trainer) \
        .set_tuner_class(StdTunerWrapper) \
        .build()

model = EnsemblePipeline.Builder() \
        .set_pipeline(model) \
        .set_num_ensembles(num_ensembles) \
        .set_horizon_len(time_horizon) \
        .build()

model.fit()
torch.save(model.state_dict(), MODEL_PATH + ".pth")

In [6]:
from experiments.iter1.util.evaluate import evaluate_model

import numpy as np
import pandas as pd
from src.util.power_splitter import PowerSplitter
from src.util.plotly import plot_results
from src.pipelines.normalizers.min_max_normalizer import MinMaxNormalizer
from src.util.evaluator import Evaluator

df = pd.read_csv(nist_path)

cleaner = TempCleaner(clean_pow_low, clean_in_low, clean_in_high, clean_out_low, clean_out_high, clean_delta_temp)
splitter = StdSplitter(train_days, val_days, test_days)
    
model = LSTM(hidden_size, num_layers, input_size, time_horizon, dropout)
trainer = TrainerWrapper(L.Trainer, 
                         max_epochs=num_epochs, 
                         callbacks=[ConditionalEarlyStopping(threshold=early_stopping_threshold)], 
                         gradient_clip_val=gradient_clipping)
optimizer = OptimizerWrapper(optim.Adam, model, lr=learning_rate)

model = DeterministicPipeline.Builder() \
        .add_data(df) \
        .set_cleaner(cleaner) \
        .set_normalizer_class(MinMaxNormalizer) \
        .set_splitter(splitter) \
        .set_sequencer_class(TimeSequencer) \
        .set_target_column(TARGET_COLUMN) \
        .set_model(model) \
        .set_optimizer(optimizer) \
        .set_batch_size(batch_size) \
        .set_seq_len(seq_len) \
        .set_worker_num(NUM_WORKERS) \
        .set_error(NRMSE) \
        .set_trainer(trainer) \
        .set_tuner_class(StdTunerWrapper) \
        .build()

model = EnsemblePipeline.Builder() \
        .set_pipeline(model) \
        .set_num_ensembles(num_ensembles) \
        .set_horizon_len(time_horizon) \
        .set_error(NRMSE) \
        .add_test_error(NMCRPS) \
        .add_test_error(NMLSCV) \
        .build()

model.load_state_dict(torch.load(MODEL_PATH + ".pth", weights_only=True))
model.test()


evaluate_model(model, df, splitter, cleaner, TIMESTAMP, POWER, on_limit_w, off_limit_w, consecutive_points, seq_len, time_horizon, TARGET_COLUMN, error, temp_boundary, 0.95)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Trainer already configured with model summary callbacks: [<class 'lightning.pytorch.callbacks.model_summary.ModelSummary'>]. Skipping setting a default `ModelSummary` callback.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
Train

Testing: |          | 0/? [00:00<?, ?it/s]
Testing DataLoader 0:   0%|          | 0/9 [00:00<?, ?it/s]
Testing: |          | 0/? [00:00<?, ?it/s]
Testing: |          | 0/? [00:00<?, ?it/s]
Testing: |          | 9/? [00:00<00:00, 23.59it/s]
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   NRMSE Loss: _epoch       0.9151360988616943
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   NRMSE Loss: _epoc

/home/vind/P5/experimentation/src/pipelines/probabilistic_pipeline.py:46: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

/home/vind/P5/experimentation/.venv/lib/python3.10/site-packages/lightning/pytorch/core/module.py:445: UserWarning:

You are trying to `self.log()` but the `self.trainer` reference is not registered on the model yet. This is most likely because the model hasn't been passed to the `Trainer`

/home/vind/P5/experimentation/src/pipelines/probabilistic_pipeline.py:50: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



NRMSE Loss: tensor(16.2237, dtype=torch.float64)
NRMSE Loss: tensor(17.5257, dtype=torch.float64)
NRMSE Loss: tensor(11.1817, dtype=torch.float64)
NRMSE Loss: tensor(31.1133, dtype=torch.float64)
NRMSE Loss: tensor(66.6310, dtype=torch.float64)
NRMSE Loss: tensor(67.8418, dtype=torch.float64)
NRMSE Loss: tensor(32.9403, dtype=torch.float64)
NRMSE Loss: tensor([0., 0., 0., 0.])
NRMSE Loss: tensor(15.5693, dtype=torch.float64)
NRMSE Loss: tensor(16.4283, dtype=torch.float64)
NRMSE Loss: tensor(29.4135, dtype=torch.float64)
NRMSE Loss: tensor(29.3642, dtype=torch.float64)
NRMSE Loss: tensor(27.9710, dtype=torch.float64)
NRMSE Loss: tensor(26.4901, dtype=torch.float64)
NRMSE Loss: tensor(50.2761, dtype=torch.float64)
NRMSE Loss: tensor(22.7593, dtype=torch.float64)
NRMSE Loss: tensor(21.7618, dtype=torch.float64)
NRMSE Loss: tensor(21.8843, dtype=torch.float64)
NRMSE Loss: tensor(4.8139, dtype=torch.float64)
NRMSE Loss: tensor(9.3640, dtype=torch.float64)
NRMSE Loss: tensor(31.1137, dtype=

Calculating On set...


On Mafe: 0.0
On Maofe: 0.0
On Maufe: 0.0
Calculating Off set...


Off Mafe: 2.186602870813397
Off Maofe: 0.0
Off Maufe: 2.186602870813397
